In [1]:
from shapely import LineString, Point, boundary
import geopandas as gpd
import geo_nx as gnx 
import networkx as nx 
import pandas as pd
import geo_nx.utils as utils
from networkx.utils import graphs_equal


In [2]:
bretelles = gpd.read_file("../data/BDCARTO/troncons_bret.geojson").to_crs(2154)
bretelles

NATURE                        ID                 ID_BDTOPO  \
0     Bretelle  METRROTT0000002274101961  TRONROUT0000000040747759   
1     Bretelle  METRROTT0000002274038597  TRONROUT0000000040768624   
2     Bretelle  METRROTT0000002274022540  TRONROUT0000000040804141   
3     Bretelle  METRROTT0000002274004919  TRONROUT0000002012707978   
4     Bretelle  METRROTT0000002274014645  TRONROUT0000000040825778   
...        ...                       ...                       ...   
2154  Bretelle  METRROTT0000002273993511  TRONROUT0000000040882357   
2155  Bretelle  METRROTT0000002274009269  TRONROUT0000000040839200   
2156  Bretelle  METRROTT0000002269916278  TRONROUT0000000333911617   
2157  Bretelle  METRROTT0000002269916300  TRONROUT0000000038086135   
2158  Bretelle  METRROTT0000002265529690  TRONROUT0000000213040876   

              SENS                                           geometry  
0      Sens direct  LINESTRING (824880.1 6288328.4, 824884.8 62883...  
1      Sens direct  LINESTRING (847746.1 6283672.8, 847818.8 62836...  
2      Sens direct  LINESTRING (881037.7 6275175.1, 881109.1 62751...  
3      Sens direct  LINESTRING (894581.5 6266428.1, 894712.3 62663...  
4      Sens direct  LINESTRING (899460.3 6271315.8, 899388.4 62712...  
...            ...                                                ...  
2154  Sens inverse  LINESTRING (880972.9 6261335.5, 880993.6 62615...  
2155   Sens direct  LINESTRING (879543 6268273.7, 879528.5 6268336...  
2156  Sens inverse  LINESTRING (835810.2 6353857, 835794.9 6353847...  
2157  Sens inverse  LINESTRING (835769.7 6353882, 835807.9 6353867.9)  
2158   Sens direct  LINESTRING (1045415 6302194.4, 1045429.1 63021...  

[2159 rows x 5 columns]

In [3]:
gr_bret = gnx.from_geopandas_edgelist(bretelles, edge_attr=True)
nx.set_node_attributes(gr_bret, "bretelle", name="nature")

In [4]:
chaussees = gpd.read_file("../data/BDCARTO/troncons_chau.geojson").to_crs(2154)
chaussees

NATURE                        ID  \
0      Route à 2 chaussées  METRROTT0000002292854059   
1      Route à 2 chaussées  METRROTT0000002292854072   
2      Route à 2 chaussées  METRROTT0000002291973331   
3      Route à 2 chaussées  METRROTT0000002321377163   
4      Route à 2 chaussées  METRROTT0000002292854067   
...                    ...                       ...   
17220     Type autoroutier  METRROTT0000002273978938   
17221     Type autoroutier  METRROTT0000002273986749   
17222     Type autoroutier  METRROTT0000002273987725   
17223     Type autoroutier  METRROTT0000002273057694   
17224     Type autoroutier  METRROTT0000002265497219   

                                               ID_BDTOPO         SENS  \
0      TRONROUT0000002287582269/TRONROUT0000002287582270  Double sens   
1      TRONROUT0000002285541866/TRONROUT0000002285541867  Double sens   
2                               TRONROUT0000000074262190  Sens direct   
3      TRONROUT0000000040987880/TRONROUT0000002277325586  Double sens   
4      TRONROUT0000000074289853/TRONROUT0000000252661385  Double sens   
...                                                  ...          ...   
17220  TRONROUT0000000040915398/TRONROUT0000000040915396  Double sens   
17221  TRONROUT0000000040896033/TRONROUT0000000040896036  Double sens   
17222  TRONROUT0000000040891128/TRONROUT0000000040891044  Double sens   
17223  TRONROUT0000000075203650/TRONROUT0000000075203651  Double sens   
17224  TRONROUT0000000074279183/TRONROUT0000000074279156  Double sens   

                                                geometry  
0      LINESTRING (1017871 6277628.4, 1017748.7 62776...  
1      LINESTRING (1044166 6300633.7, 1044158.1 63006...  
2      LINESTRING (1051812.4 6307811.9, 1051832.5 630...  
3      LINESTRING (907481.5 6238495.2, 907511.3 62384...  
4      LINESTRING (1044753.3 6298676.4, 1044781.7 629...  
...                                                  ...  
17220  LINESTRING (888097.7 6255434.4, 888154.9 6255297)  
17221  LINESTRING (887219.7 6258788.1, 887264.9 62587...  
17222  LINESTRING (888961.8 6259195.8, 888973.5 62591...  
17223  LINESTRING (968458.8 6260913.4, 968339.6 62610...  
17224  LINESTRING (1041999.6 6302088.3, 1041846.5 630...  

[17225 rows x 5 columns]

In [5]:
gr_chau = gnx.from_geopandas_edgelist(chaussees, edge_attr=True)
nx.set_node_attributes(gr_chau, "chaussees", name="nature")

sub = nx.subgraph_view(gr_chau, filter_edge=lambda x, y: gr_chau[x][y]['NATURE'] == 'Type autoroutier')
gr_auto = nx.induced_subgraph(sub, nx.utils.flatten(sub.edges()))

In [6]:
refnat = {'tiles': 'cartodbpositron', 'location': [46.3, 2.3], 'zoom_start': 7}
#param_exp_nd = {'n_marker_kwds': {'radius': 3, 'fill': True}}
param_exp_gr = {'e_popup': ['weight', 'source', 'target', 'NATURE'], 'e_tooltip': ["source", "target"], 
                'n_tooltip': ["node_id", "nature"], 'n_marker_kwds': {'radius': 1, 'fill': False}}
param_exp_auto = {'e_popup': ['weight', 'source', 'target', 'NATURE', 'SENS'], 'e_tooltip': ["source", "target"], 
                'n_tooltip': ["node_id", "nature"], 'n_marker_kwds': {'radius': 1, 'fill': False}}

carte = gr_bret.explore(refmap=refnat, n_color='black', e_name='edges bretelles', n_name='nodes bretelles', **param_exp_gr)
carte = gr_auto.explore(refmap=carte, e_color='green', e_name='edges chaussees', n_name='nodes chaussees', n_color='black', layercontrol=True, **param_exp_auto)
#carte = gr_nat.explore(refmap=carte, e_color='magenta', e_name='edges nat', n_name='nodes nat',  n_color='black', **param_exp_gr)
#carte = gr_autoroute.explore(refmap=carte, e_color='cyan', e_name='edges auto', n_name='nodes auto', layercontrol=True, n_color='black', **param_exp_gr)
carte

In [ ]:
sub_euro = nx.subgraph_view(gr, filter_edge=lambda x,y: gr[x][y]["TYPE_ROUTE"] == 'Route européenne')
gr_euro =  nx.induced_subgraph(sub_euro, nx.utils.flatten(sub_euro.edges()))
len(gr_euro.edges)

In [ ]:
sub_auto = nx.subgraph_view(gr, filter_edge=lambda x,y: gr[x][y]["TYPE_ROUTE"] == 'Autoroute')
gr_autoroute =  nx.induced_subgraph(sub_auto, nx.utils.flatten(sub_auto.edges()))

In [ ]:
sub_nat = nx.subgraph_view(gr, filter_edge=lambda x,y: gr[x][y]["TYPE_ROUTE"] == 'Nationale')
gr_nat =  nx.induced_subgraph(sub_nat, nx.utils.flatten(sub_nat.edges()))

In [ ]:
refnat = {'tiles': 'cartodbpositron', 'location': [46.3, 2.3], 'zoom_start': 7}
param_exp_nd = {'n_marker_kwds': {'radius': 3, 'fill': True}}
param_exp_gr = {'e_popup': ['weight', 'source', 'target', 'TYPE_ROUTE'], 'e_tooltip': ["source", "target", "TYPE_ROUTE"], 
                'n_tooltip': ["node_id"], 'n_marker_kwds': {'radius': 1, 'fill': False}}


carte = gr.explore(refmap=refnat, n_color='black', e_name='edges gr', n_name='nodes gr', **param_exp_gr)
carte = gr_euro.explore(refmap=carte, e_color='green', e_name='edges euro', n_name='nodes euro', n_color='black', **param_exp_gr)
carte = gr_nat.explore(refmap=carte, e_color='magenta', e_name='edges nat', n_name='nodes nat',  n_color='black', **param_exp_gr)
carte = gr_autoroute.explore(refmap=carte, e_color='cyan', e_name='edges auto', n_name='nodes auto', layercontrol=True, n_color='black', **param_exp_gr)
carte

In [ ]:
print(Point(bretelles.iloc[1334]['geometry'].coords[-1]))

In [ ]:
print(bretelles.iloc[1334]['geometry'].boundary.geoms[0])

In [ ]:
print(bretelles.iloc[1335]['geometry'].boundary)
boundary(bretelles.iloc[1335]['geometry']) is None
if not bretelles.iloc[1335]['geometry'].boundary:
    print('empty')

In [ ]:
for i in range(len(bretelles)):
    print(i, bretelles.iloc[i]['geometry'].boundary.geoms[0])

In [ ]:
GEOM = 'geometry'
#bretelles['geometry']
bretelles["source_geo"] = bretelles[GEOM].apply(lambda ls: ls.boundary.geoms[0])

In [ ]:
 n_gdf, e_gdf = utils.nodes_gdf_from_edges_gdf(bretelles)